# EuroPython 2015, Stefan Behnel

See http://consulting.behnel.de/

In [1]:
%load_ext cython

In [2]:
import sys
import Cython
print("Python %d.%d.%d %s %s" % sys.version_info)
print("Cython %s" % Cython.__version__)

Python 3.5.0 beta 3
Cython 0.23.beta1


# Functions and Coercion

In [3]:
%%cython

def pyfunc(x):
    return x + 1

def cyfunc(int x):
    return x + 1

cdef int cfunc(int x):
    return x + 1

cpdef cypyfunc(int x):
    y = cfunc(x + 1)
    return y * 2

In [4]:
pyfunc(2)

3

In [5]:
cyfunc(2)

3

In [6]:
cfunc(2)

NameError: name 'cfunc' is not defined

In [7]:
cypyfunc(2)

8

# Function "JIT compiling"

In [8]:
# NOTE: Python code!

import cython

@cython.compile
def calc(a, b):
    for x in range(a):
        b += x
    return b
    

In [9]:
calc(10, 20)

65

In [10]:
type(calc)

Cython.Build.Inline.RuntimeCompiledFunction

# Calling C functions

In [11]:
%%cython -a
# libc math functions
from libc cimport math

print( math.sin(math.M_PI / 2) )


1.0


In [12]:
%%cython
# dynamic C memory allocation
from libc.stdlib cimport malloc, free

cdef int* cmem = <int*>malloc(22 * sizeof(int))
if not cmem:
    raise MemoryError()
free(cmem)


In [13]:
%%cython
# dynamic CPython heap memory allocation
from cpython.mem cimport PyMem_Malloc, PyMem_Free

cdef int* pymem = <int*>PyMem_Malloc(22 * sizeof(int))
if not pymem:
    raise MemoryError()
    
try:
    pymem[:] = [1,2,3]
    print( pymem[0] + pymem[2] )
finally:
    PyMem_Free(pymem)


4


# Auto-wrapping C functions to Python

In [14]:
%%cython -a
from libc cimport math, stdlib
py_sin = math.sin
py_atoi = stdlib.atoi

In [15]:
py_sin(1/2)

0.479425538604203

In [16]:
py_atoi(b'123')

123

# External libraries

In [17]:
%%cython
# distutils: include_dirs=/usr/include/luajit-2.0
# distutils: libraries=luajit-5.1

## distutils: include_dirs=/usr/include/lua5.1
## distutils: libraries=lua5.1

cdef extern from "lua.h":
    ctypedef struct lua_State
    lua_State *luaL_newstate ()
    void lua_close (lua_State *L)
    int luaL_loadbuffer (lua_State *L, char *buff, size_t sz, char *name)
    void lua_settop (lua_State *L, int idx)
    int lua_gettop (lua_State *L)
    int lua_pcall (lua_State *L, int nargs, int nresults, int errfunc)
    int lua_type (lua_State *L, int idx)
    float lua_tonumber (lua_State *L, int idx)
    enum:
        LUA_TNUMBER
        LUA_MULTRET


def run_lua(code):
    cdef int result_status
    cdef float result

    if isinstance(code, unicode):
        code = code.encode('utf8')
    elif not isinstance(code, bytes):
        raise ValueError("code must be a string")

    # init Lua runtime
    L = luaL_newstate()
    if not L:
        raise MemoryError()

    try:
        # compile Lua code
        if luaL_loadbuffer(L, code, len(code), '<python>'):
            raise SyntaxError()

        # execute code
        if lua_pcall(L, 0, LUA_MULTRET, 0):
            raise RuntimeError()

        # convert return value (Lua number == float)
        assert lua_type(L, 1) == LUA_TNUMBER, "not a numeric return value"
        return lua_tonumber(L, 1)
    finally:
        lua_settop(L, 0)
        lua_close(L)


In [18]:
code = '''
function fib(i)
    if i > 2 then
        return fib(i-1) + fib(i-2)
    else
        return 1
    end
end
'''

run_lua(code + "return fib(10)")

55.0

In [19]:
%%timeit bench = code + "return fib(24)"

run_lua(bench)

100 loops, best of 3: 2.15 ms per loop


In [20]:
# distutils: include_dirs=/usr/include/luajit-2.0
# distutils: libraries=luajit-5.1


# C arrays

In [21]:
%%cython -a
def carrays():
    cdef int[10] a, b
    a[:5] = [1,2,3,4,5]
    b = a
    b[5:] = [6,7,8,9,10]

    for i in b[:3]:
        print(i+1)

    return b

In [22]:
carrays()

2
3
4


[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

# C tuples

In [23]:
%%cython -a

def ctuples():
    cdef int a = 42
    cdef double b = a / 5.0

    cdef (int, double) t = (a, b)
    print(t[0])
    print(t[1])
    print(t)

    return t


In [24]:
ctuples()

42
8.4
(42, 8.4)


(42, 8.4)

# C++

In [25]:
%%cython -a
# distutils: language=c++


from libcpp.vector cimport vector

def func():
    cdef vector[int] v
    v.push_back(10)
    return v


In [26]:
func()

[10]

In [27]:
%%cython -a
# distutils: language=c++

from libcpp.vector cimport vector

cdef class Integers:
    cdef vector[int] _values

    def add(self, int value):
        self._values.push_back(value)

    def __repr__(self):
        return repr(self._values)


In [28]:
x = Integers()
x.add(2)
x.add(3)
x

[2, 3]